In [1]:
import numpy as np
import pandas as pd
import ray
from configs.load_specific_data import pharma_basket
from env.multi_agent.worker_single_stock import Worker
from ray.rllib.utils import check_env
from ray.train.rl import RLTrainer
from ray.air.config import RunConfig, ScalingConfig
from ray.rllib.algorithms.bc.bc import BC
from ray.rllib.algorithms import a2c
from ray.tune.registry import register_env
import gymnasium
ray.init(_temp_dir='/Users/floriankockler/rayresults/')
import warnings
warnings.simplefilter(action='ignore', category=Warning)
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter(action='ignore', category=DeprecationWarning)
import os
os.environ['PYTHONWARNINGS'] = 'ignore'

2023-09-03 22:11:17,533	WARNING deprecation.py:50 -- DeprecationWarning: `DirectStepOptimizer` has been deprecated. This will raise an error in the future!
2023-09-03 22:11:20,201	INFO worker.py:1612 -- Started a local Ray instance. View the dashboard at 127.0.0.1:8265 


In [2]:
train_df, validate_df, test_df, stock_dimension, state_space, indicators = pharma_basket()
train_df = train_df[train_df["tic"] == "PFE.US"]
validate_df = validate_df[validate_df["tic"] == "PFE.US"]


In [3]:
worker_config =   {
        "cash_initial": 1000000, 
        "trading_cost": 0.001, 
        "tech_indicator_list": indicators,
        "print_verbosity": 1,
        "initial_shares_held": 0,
        "df": train_df,  }


env = Worker(env_config=worker_config)
check_env(env)

In [4]:


worker_config =   {
        "cash_initial": 1000000, 
        "trading_cost": 0.001, 
        "tech_indicator_list": indicators,
        "print_verbosity": 1,
        "initial_shares_held": 0,
        "df": train_df,  }


env = Worker(env_config=worker_config)

n_iterations = 13000

state = env.reset()

for _ in range(n_iterations):

    action = env.action_space.sample()

    obs, reward, done, truncated, info= env.step(action)

    # print(f"Action: {action}, Reward: {reward}, Portfolio Value: {obs[0] + obs[1] * obs[2]}")
    
    if done:
        print("Episode finished!")
        state = env.reset()
    else:
        state = obs

day: 6304, episode: 1
total_pnl: 2030935.12
self.cash_spent: 1431313942.74
self.cash_from_sales: 1430405252.56
total_cost: 2861721.00
total_trades: 4247
Begin_portfolio_value: 1000000.0
End stock holdings: 283433
Last stock price: 10.371500015258789
End_portfolio_value: 3030933.0
Invalid Actions 1
Episode finished!
day: 6304, episode: 2
total_pnl: -896995.62
self.cash_spent: 91187110.20
self.cash_from_sales: 90290073.10
total_cost: 181476.55
total_trades: 4223
Begin_portfolio_value: 1000000.0
End stock holdings: 4
Last stock price: 10.371500015258789
End_portfolio_value: 103004.1796875
Invalid Actions 0
Episode finished!


In [6]:
def env_creator(env_config):
    # Assuming this is your environment
    return Worker(env_config)

register_env("Single_Stock", env_creator)

worker_config =   {
        "cash_initial": 1000000, 
        "trading_cost": 0.001, 
        "tech_indicator_list": indicators,
        "print_verbosity": 1,
        "initial_shares_held": 0,
        "df": train_df,  
        }


trainer = RLTrainer(
    run_config=RunConfig(stop={"training_iteration": 5},local_dir="/Users/floriankockler/rayresults/training"),
    scaling_config=ScalingConfig(
        num_workers=3,
        use_gpu=False,
    ),

    algorithm=a2c.A2C,
    config={
        "env": "Single_Stock",
        "env_config": worker_config,
        "framework": "tf",
        "evaluation_num_workers": 1,
        "evaluation_interval": 1,
        "evaluation_config": {"input": "sampler"},
    },
)
result = trainer.fit()

(pid=12195) DeprecationWarning: `DirectStepOptimizer` has been deprecated. This will raise an error in the future!
(AIRA2C pid=12195) 2023-09-03 21:46:14,711	WARNING deprecation.py:50 -- DeprecationWarning: `rllib/algorithms/a2c/` has been deprecated. Use `rllib_contrib/a2c/` instead. This will raise an error in the future!
(AIRA2C pid=12195) 2023-09-03 21:46:14,712	WARNING deprecation.py:50 -- DeprecationWarning: `rllib/algorithms/a3c/` has been deprecated. Use `rllib_contrib/a3c/` instead. This will raise an error in the future!
(AIRA2C pid=12195) 2023-09-03 21:46:14,712	WARNING algorithm_config.py:656 -- Cannot create A2CConfig from given `config_dict`! Property __stdout_file__ not supported.
(pid=12217) DeprecationWarning: `DirectStepOptimizer` has been deprecated. This will raise an error in the future!
(pid=12216) DeprecationWarning: `DirectStepOptimizer` has been deprecated. This will raise an error in the future!
(RolloutWorker pid=12216) 2023-09-03 21:46:22,597	WARNING depreca

(RolloutWorker pid=12284) day: 6304, episode: 3
(RolloutWorker pid=12284) total_pnl: 3158637.25
(RolloutWorker pid=12284) self.cash_spent: 866404463.47
(RolloutWorker pid=12284) self.cash_from_sales: 865419551.56
(RolloutWorker pid=12284) total_cost: 1731824.50
(RolloutWorker pid=12284) total_trades: 3615
(RolloutWorker pid=12284) Begin_portfolio_value: 1000000.0
(RolloutWorker pid=12284) End stock holdings: 399513
(RolloutWorker pid=12284) Last stock price: 10.371500015258789
(RolloutWorker pid=12284) End_portfolio_value: 4158638.0
(RolloutWorker pid=12284) Invalid Actions 129
(RolloutWorker pid=12284) =================================


(RolloutWorker pid=12284) 2023-09-03 21:46:44,120	WARNING env_runner_v2.py:155 -- More than 6305 observations in 6305 env steps for episode 642059558108855869 are buffered in the sampler. If this is more than you expected, check that that you set a horizon on your environment correctly and that it terminates at some point. Note: In multi-agent environments, `rollout_fragment_length` sets the batch size based on (across-agents) environment steps, not the steps of individual agents, which can result in unexpectedly large batches.Also, you may be waiting for your Env to terminate (batch_mode=`complete_episodes`). Make sure it does at some point.


(RolloutWorker pid=12284) day: 6304, episode: 4
(RolloutWorker pid=12284) total_pnl: 40059.65
(RolloutWorker pid=12284) self.cash_spent: 13591779.97
(RolloutWorker pid=12284) self.cash_from_sales: 13621011.77
(RolloutWorker pid=12284) total_cost: 27212.85
(RolloutWorker pid=12284) total_trades: 3593
(RolloutWorker pid=12284) Begin_portfolio_value: 1000000.0
(RolloutWorker pid=12284) End stock holdings: 1044
(RolloutWorker pid=12284) Last stock price: 10.371500015258789
(RolloutWorker pid=12284) End_portfolio_value: 55148.67578125
(RolloutWorker pid=12284) Invalid Actions 164
(RolloutWorker pid=12284) =================================
(RolloutWorker pid=12284) day: 6304, episode: 5
(RolloutWorker pid=12284) total_pnl: 77026.64
(RolloutWorker pid=12284) self.cash_spent: 30029360.69
(RolloutWorker pid=12284) self.cash_from_sales: 30066747.46
(RolloutWorker pid=12284) total_cost: 60096.15
(RolloutWorker pid=12284) total_trades: 3581
(RolloutWorker pid=12284) Begin_portfolio_value: 1000000.

False


In [5]:
from ray import tune
from ray.tune import CLIReporter
from ray.rllib.algorithms.a2c import A2CConfig
config = A2CConfig()

reporter = CLIReporter(max_progress_rows=10)
worker_config =   {
        "cash_initial": 1000000, 
        "trading_cost": 0.001, 
        "tech_indicator_list": indicators,
        "print_verbosity": 1,
        "initial_shares_held": 0,
        "df": train_df,  }


static_config = {
    "log_level": 'DEBUG',
    "env": Worker,
    "env_config": worker_config,
    "evaluation_config": {
        "env_config": {
            "df": validate_df,
        }
    },
    "evaluation_num_episodes": 10
}

search_space = {
    "lr": tune.loguniform(0.00001, 0.0001),
    "gamma": tune.uniform(0.95, 0.9999),
    "entropy_coeff": tune.loguniform(0.01, 0.1),
    "vf_loss_coeff": tune.uniform(0.1, 0.5),
    "lambda": tune.uniform(0.9, 1.0),
    "num_steps": tune.choice([50, 100, 200, 500, 1000]),

}

# Merge the two configurations
config = {**static_config, **search_space}
# config = {**static_config}

tune.run(
    "A2C",
    stop={"training_iteration": 150},
    config=config,
    num_samples=10,


  
    # scheduler=async_hyperband, 
    checkpoint_config={
        "num_to_keep": 3,
        "checkpoint_score_attribute": "mean_reward",
        "checkpoint_at_end": "True",
    },
    progress_reporter=reporter,
    local_dir="/Users/floriankockler/rayresults/Single_Trading8/"
)

2023-09-03 22:11:23,793	INFO tune.py:657 -- [output] This uses the legacy output and progress reporter, as Jupyter notebooks are not supported by the new engine, yet. For more information, please see https://github.com/ray-project/ray/issues/36949
2023-09-03 22:11:23,794	WARNING syncer.py:260 -- You are using remote storage, but you don't have `fsspec` installed. This can lead to inefficient syncing behavior. To avoid this, install fsspec with `pip install fsspec`. Depending on your remote storage provider, consider installing the respective fsspec-package (see https://github.com/fsspec).
2023-09-03 22:11:23,836	WARNING deprecation.py:50 -- DeprecationWarning: `build_tf_policy` has been deprecated. This will raise an error in the future!
2023-09-03 22:11:23,850	WARNING deprecation.py:50 -- DeprecationWarning: `build_policy_class` has been deprecated. This will raise an error in the future!
2023-09-03 22:11:23,913	WARNING algorithm_config.py:2534 -- Setting `exploration_config={}` becau

== Status ==
Current time: 2023-09-03 22:11:24 (running for 00:00:00.64)
Using FIFO scheduling algorithm.
Logical resource usage: 6.0/8 CPUs, 0/0 GPUs
Result logdir: /Users/floriankockler/rayresults/Single_Trading8/A2C
Number of trials: 10/10 (10 PENDING)
+------------------------+----------+-------+-----------------+----------+----------+-------------+-------------+-----------------+
| Trial name             | status   | loc   |   entropy_coeff |    gamma |   lambda |          lr |   num_steps |   vf_loss_coeff |
|------------------------+----------+-------+-----------------+----------+----------+-------------+-------------+-----------------|
| A2C_Worker_0e415_00000 | PENDING  |       |       0.017931  | 0.981861 | 0.958142 | 1.29364e-05 |         100 |        0.464733 |
| A2C_Worker_0e415_00001 | PENDING  |       |       0.0423398 | 0.953955 | 0.92539  | 6.69784e-05 |         200 |        0.431859 |
| A2C_Worker_0e415_00002 | PENDING  |       |       0.0256884 | 0.961206 | 0.952325 

(pid=17297) DeprecationWarning: `DirectStepOptimizer` has been deprecated. This will raise an error in the future!
(A2C pid=17297) 2023-09-03 22:11:30,495	WARNING deprecation.py:50 -- DeprecationWarning: `rllib/algorithms/a2c/` has been deprecated. Use `rllib_contrib/a2c/` instead. This will raise an error in the future!
(A2C pid=17297) 2023-09-03 22:11:30,495	WARNING deprecation.py:50 -- DeprecationWarning: `rllib/algorithms/a3c/` has been deprecated. Use `rllib_contrib/a3c/` instead. This will raise an error in the future!
(A2C pid=17297) 2023-09-03 22:11:30,495	WARNING algorithm_config.py:656 -- Cannot create A2CConfig from given `config_dict`! Property num_steps not supported.
(A2C pid=17297) 2023-09-03 22:11:30,495	WARNING deprecation.py:50 -- DeprecationWarning: `AlgorithmConfig.evaluation(evaluation_num_episodes=..)` has been deprecated. Use `AlgorithmConfig.evaluation(evaluation_duration=.., evaluation_duration_unit='episodes')` instead. This will raise an error in the future!


== Status ==
Current time: 2023-09-03 22:11:34 (running for 00:00:10.94)
Using FIFO scheduling algorithm.
Logical resource usage: 6.0/8 CPUs, 0/0 GPUs
Result logdir: /Users/floriankockler/rayresults/Single_Trading8/A2C
Number of trials: 10/10 (10 PENDING)
+------------------------+----------+-------+-----------------+----------+----------+-------------+-------------+-----------------+
| Trial name             | status   | loc   |   entropy_coeff |    gamma |   lambda |          lr |   num_steps |   vf_loss_coeff |
|------------------------+----------+-------+-----------------+----------+----------+-------------+-------------+-----------------|
| A2C_Worker_0e415_00000 | PENDING  |       |       0.017931  | 0.981861 | 0.958142 | 1.29364e-05 |         100 |        0.464733 |
| A2C_Worker_0e415_00001 | PENDING  |       |       0.0423398 | 0.953955 | 0.92539  | 6.69784e-05 |         200 |        0.431859 |
| A2C_Worker_0e415_00002 | PENDING  |       |       0.0256884 | 0.961206 | 0.952325 

(pid=17313) DeprecationWarning: `DirectStepOptimizer` has been deprecated. This will raise an error in the future! [repeated 2x across cluster] (Ray deduplicates logs by default. Set RAY_DEDUP_LOGS=0 to disable log deduplication, or see https://docs.ray.io/en/master/ray-observability/ray-logging.html#log-deduplication for more options.)
(A2C pid=17298) 2023-09-03 22:11:30,495	WARNING deprecation.py:50 -- DeprecationWarning: `rllib/algorithms/a3c/` has been deprecated. Use `rllib_contrib/a3c/` instead. This will raise an error in the future! [repeated 2x across cluster]
(A2C pid=17298) 2023-09-03 22:11:30,495	WARNING algorithm_config.py:656 -- Cannot create A2CConfig from given `config_dict`! Property num_steps not supported.
(A2C pid=17298) 2023-09-03 22:11:30,495	WARNING deprecation.py:50 -- DeprecationWarning: `AlgorithmConfig.evaluation(evaluation_num_episodes=..)` has been deprecated. Use `AlgorithmConfig.evaluation(evaluation_duration=.., evaluation_duration_unit='episodes')` inst

...

== Status ==
Current time: 2023-09-04 00:19:25 (running for 02:08:01.83)
Using FIFO scheduling algorithm.
Logical resource usage: 6.0/8 CPUs, 0/0 GPUs
Result logdir: /Users/floriankockler/rayresults/Single_Trading8/A2C
Number of trials: 10/10 (2 RUNNING, 8 TERMINATED)
+------------------------+------------+-----------------+-----------------+----------+----------+-------------+-------------+-----------------+--------+------------------+---------+----------+----------------------+----------------------+--------------------+
| Trial name             | status     | loc             |   entropy_coeff |    gamma |   lambda |          lr |   num_steps |   vf_loss_coeff |   iter |   total time (s) |      ts |   reward |   episode_reward_max |   episode_reward_min |   episode_len_mean |
|------------------------+------------+-----------------+-----------------+----------+----------+-------------+-------------+-----------------+--------+------------------+---------+----------+-------------------

(A2C pid=42626) 2023-09-04 00:19:30,198	DEBUG train_ops.py:164 -- == sgd epochs for default_policy == [repeated 417x across cluster]


== Status ==
Current time: 2023-09-04 00:19:30 (running for 02:08:06.86)
Using FIFO scheduling algorithm.
Logical resource usage: 6.0/8 CPUs, 0/0 GPUs
Result logdir: /Users/floriankockler/rayresults/Single_Trading8/A2C
Number of trials: 10/10 (2 RUNNING, 8 TERMINATED)
+------------------------+------------+-----------------+-----------------+----------+----------+-------------+-------------+-----------------+--------+------------------+---------+----------+----------------------+----------------------+--------------------+
| Trial name             | status     | loc             |   entropy_coeff |    gamma |   lambda |          lr |   num_steps |   vf_loss_coeff |   iter |   total time (s) |      ts |   reward |   episode_reward_max |   episode_reward_min |   episode_len_mean |
|------------------------+------------+-----------------+-----------------+----------+----------+-------------+-------------+-----------------+--------+------------------+---------+----------+-------------------

2023-09-04 00:19:31,414	ERROR checkpoint_manager.py:402 -- Result dict has no key: mean_reward. checkpoint_score_attr must be set to a key in the result dict. Valid keys are: ['episode_reward_max', 'episode_reward_min', 'episode_reward_mean', 'episode_len_mean', 'episodes_this_iter', 'num_faulty_episodes', 'num_healthy_workers', 'num_in_flight_async_reqs', 'num_remote_worker_restarts', 'num_agent_steps_sampled', 'num_agent_steps_trained', 'num_env_steps_sampled', 'num_env_steps_trained', 'num_env_steps_sampled_this_iter', 'num_env_steps_trained_this_iter', 'num_env_steps_sampled_throughput_per_sec', 'num_env_steps_trained_throughput_per_sec', 'timesteps_total', 'num_steps_trained_this_iter', 'agent_timesteps_total', 'done', 'episodes_total', 'training_iteration', 'trial_id', 'date', 'timestamp', 'time_this_iter_s', 'time_total_s', 'pid', 'hostname', 'node_ip', 'time_since_restore', 'iterations_since_restore', 'experiment_tag', 'info/num_env_steps_sampled', 'info/num_env_steps_trained',

== Status ==
Current time: 2023-09-04 00:19:32 (running for 02:08:08.63)
Using FIFO scheduling algorithm.
Logical resource usage: 3.0/8 CPUs, 0/0 GPUs
Result logdir: /Users/floriankockler/rayresults/Single_Trading8/A2C
Number of trials: 10/10 (10 TERMINATED)
+------------------------+------------+-----------------+-----------------+----------+----------+-------------+-------------+-----------------+--------+------------------+---------+----------+----------------------+----------------------+--------------------+
| Trial name             | status     | loc             |   entropy_coeff |    gamma |   lambda |          lr |   num_steps |   vf_loss_coeff |   iter |   total time (s) |      ts |   reward |   episode_reward_max |   episode_reward_min |   episode_len_mean |
|------------------------+------------+-----------------+-----------------+----------+----------+-------------+-------------+-----------------+--------+------------------+---------+----------+----------------------+------